In [12]:
import pandas as pd 
from ydata_profiling import ProfileReport
import matplotlib.pyplot as plt
import numpy as np



In [ ]:
survey = pd.read_csv('salary_survey.csv')
set = survey.copy()

In [2]:
new_columns_name = {'How old are you?': 'age range',
                    'What industry do you work in?': 'Industry',
                    'If your job title needs additional context, please clarify here:' :'Add context',
                    "What is your annual salary? (You'll indicate the currency in a later question. If you are part-time or hourly, please enter an annualized equivalent -- what you would earn if you worked the job 40 hours a week, 52 weeks a year.)" : 'salary',
                    'How much additional monetary compensation do you get, if any (for example, bonuses or overtime in an average year)? Please only include monetary compensation here, not the value of benefits.' : 'compensation',
                    'Please indicate the currency' : 'Currency',
                    'If "Other," please indicate the currency here: ' : 'Other currency',
                    'If your income needs additional context, please provide it here:' : 'income context',
                    'What country do you work in?' : 'Country of work',
                    "If you're in the U.S., what state do you work in?" : 'US State',
                    'What city do you work in?':'city',
                    'How many years of professional work experience do you have overall?' : 'Overall experience',
                    'How many years of professional work experience do you have in your field?' : 'Field experience',
                    'What is your highest level of education completed?':'Education',
                    'What is your gender?' : 'Gender',
                    'What is your race? (Choose all that apply.)' :'Race'
                }
set.rename(columns=new_columns_name, inplace=True)

In [3]:
df = set.copy()
set.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 28014 entries, 0 to 28013
Data columns (total 18 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   Timestamp           28014 non-null  object 
 1   age range           28014 non-null  object 
 2   Industry            27941 non-null  object 
 3   Job title           28013 non-null  object 
 4   Add context         7249 non-null   object 
 5   salary              28014 non-null  object 
 6   compensation        20734 non-null  float64
 7   Currency            28014 non-null  object 
 8   Other currency      199 non-null    object 
 9   income context      3037 non-null   object 
 10  Country of work     28014 non-null  object 
 11  US State            23010 non-null  object 
 12  city                27933 non-null  object 
 13  Overall experience  28014 non-null  object 
 14  Field experience    28014 non-null  object 
 15  Education           27797 non-null  object 
 16  Gend

In [4]:
profile = ProfileReport(set, title= "Profile Report")
profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [101]:
def preprocessing(df):
        
        #remove the timestamp column as majority of data were collected in 2021
        df.drop('Timestamp', axis=1, inplace=True)
        
        #remove 2 age range categories: 65 or over and under 18 as it makes less than 1% of the dataset
        df = df[~df['age range'].isin(['65 or over','under 18'])]
        
        #keep only top 12 popular industries, the remaining go to new category called 'Others'
        top_industries = df['Industry'].value_counts().head(12).index
        df['Industry'] = df['Industry'].apply(lambda x: x if x in top_industries else 'Others')
        
        #drop columns 'job title' and 'Add context' 
        df.drop(['Job title', 'Add context'], axis=1, inplace=True)
        
        # Fill missing values in 'compensation' with 0 
        df['compensation'].fillna(0, inplace= True)
        # Categorize the values in 4 ranges into a new column
        df['compensation_cat'] = pd.cut(df['compensation'],
                                        bins= [-1,0,10000,20000, float('inf')],
                                        labels=['0',
                                                'above 0 -10k',
                                                'above 10k-20k',
                                                'above 20k'],
                                        right= True)
        #drop 'compensation' column
        df.drop('compensation', axis=1, inplace=True)
        
        
        #remove ',' in salary values and convert into float type    
        df['salary'] = df.loc[:,'salary'].str.replace(',','')
        df['salary'] = df.loc[:,'salary'].astype(float)
        #only keep top 5 currencies
        top_currencies = df['Currency'].value_counts().head(5).index
        df = df[df['Currency'].isin(top_currencies)]
                        
        #create an exchange rate dict, data from google
        exchange_rates = {
                        'USD': 1,       #do nothing
                        'CAD': 0.78,    #CAD to USD   
                        'GBP': 1.38,    #GBP to USD  
                        'EUR': 1.12,    #EUR to USD
                        'AUD': 0.72     #AUD to USD
                                        }
        #loop through rows and exchange salary into US dollar
        for index, row in df.iterrows():
                currency = row['Currency']
                salary = row['salary']
                for dict_currency, rate in exchange_rates.items():
                        if currency == dict_currency:
                                salary = salary*rate
                                df.at[index, 'salary'] = salary
        #drop the currency column
        df.drop('Currency', axis=1, inplace=True)
        
        #remove outliers in 'salary' using Winsorization method (percentage capping)
        def remove_outliers(df):
                q1 = np.percentile(df, 1)
                q3 = np.percentile(df, 99)
                return df[(df>=q1) & (df<=q3)]
        df['salary']= remove_outliers(df['salary'])
        df = df.dropna(subset=['salary'])
        
        #drop 'Other currency' and 'income context' columns
        df.drop(['Other currency', 'income context'], axis=1, inplace=True)
        
        #replace any value contains 'u' and 's' into US group, the remaining as 'Oversea'
        df['Country of work'] = df['Country of work'].apply(lambda x: 'US' if 'u' in x.lower() and 's' in x.lower() else 'Oversea')

        #drop 'US state' and 'city' column for now 
        df.drop(['US State','city'], axis=1, inplace= True)
        
        #return genders into 4 categories
        genders = df['Gender'].value_counts().head(3).index
        df['Gender'] = df['Gender'].apply(lambda x: x if x in genders else 'Not specified')
        
        #return genders into 6 categories
        races = df['Race'].value_counts().head(5).index
        df['Race'] = df['Race'].apply(lambda x: x if x in races else 'Not specified')
        
        return df
    

In [102]:
tdf=set.copy()

In [103]:

tdf = preprocessing(tdf)

C:\Users\pvdng\AppData\Local\Temp\ipykernel_13604\3610155144.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Industry'] = df['Industry'].apply(lambda x: x if x in top_industries else 'Others')
C:\Users\pvdng\AppData\Local\Temp\ipykernel_13604\3610155144.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.drop(['Job title', 'Add context'], axis=1, inplace=True)
C:\Users\pvdng\AppData\Local\Temp\ipykernel_13604\3610155144.py:17: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace met

In [104]:
tdf.head(5)

age range                       Industry   salary Country of work  \
0     25-34   Education (Higher Education)  55000.0              US   
1     25-34              Computing or Tech  75348.0         Oversea   
2     25-34  Accounting, Banking & Finance  34000.0              US   
3     25-34                     Nonprofits  62000.0              US   
4     25-34  Accounting, Banking & Finance  60000.0              US   

  Overall experience Field experience        Education      Gender   Race  \
0          5-7 years        5-7 years  Master's degree       Woman  White   
1       8 - 10 years        5-7 years   College degree  Non-binary  White   
2        2 - 4 years      2 - 4 years   College degree       Woman  White   
3       8 - 10 years        5-7 years   College degree       Woman  White   
4       8 - 10 years        5-7 years   College degree       Woman  White   

  compensation_cat  
0                0  
1     above 0 -10k  
2                0  
3     above 0 -10k  
4     above 0 -10k

In [105]:

y = tdf['salary']
X = tdf.drop('salary', axis=1)
X = pd.get_dummies(X)

In [106]:
len(X.columns)

56